# Sentiment classification in Korean

- Google trans package(googletrans)를 활용해 번역을 통해 sentiment classification
- sentiments : positive, negative
- dataset : naver sentiment movie corpus


Reference : 
- https://github.com/goodhhw1112/nlp/blob/master/nlp_learning.ipynb
- https://github.com/e9t/nsmc
- https://www.slideshare.net/langley0/textcnn-sentiment
- https://towardsdatascience.com/a-beginners-guide-on-sentiment-analysis-with-rnn-9e100627c02e


In [1]:
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation, Flatten, Conv2D, pooling, SimpleRNN, LSTM, BatchNormalization
from keras.wrappers.scikit_learn import KerasClassifier
from keras.utils import np_utils
from sklearn.model_selection import train_test_split
from sklearn import model_selection, metrics
import json
import numpy as np
import math

/Users/grace/workspace/keras/venv/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.
/Users/grace/workspace/keras/venv/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: compiletime version 3.5 of module 'tensorflow.python.framework.fast_tensor_util' does not match runtime version 3.6
  return f(*args, **kwds)


In [2]:
sample_kor = '영어 문법은 복잡하다.'
lang_ko = 'ko'
sample_eng = 'english grammer is complicated.'
lang_en = 'en'

### 전처리

- 한글
    - Okt 형태소 분석기 사용
    - 조사, 어미, 구두점, 외국어, 한글자 단어 제외
   
- 영어
    - stemming
    - lemmatization
    - remove stopwords

In [3]:
# preprocess korean & english
from konlpy.tag import Okt
# import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer, SnowballStemmer

def prep_pos(text, lang):
    if lang == 'ko':
        words = []
        # class로 변환 할것
        okt = Okt()
        sent_structrues = okt.pos(text)
        print(sent_structrues)
        for word in sent_structrues:
            # 조사, punctuation, 외래어, suffix제외
            if word[1] not in ['Josa', 'Punctuation', 'Foreign', 'Suffix'] and len(word[0])>1:
                words.append(word[0])
                
    elif lang == 'en':
        word = list(filter(lambda x: x not in stopwords.words('english') , text.replace('.', '').split()))
        print(word)
        stemmer = SnowballStemmer('english')
        lemmatizer = WordNetLemmatizer()
        words = [lemmatizer.lemmatize(stemmer.stem(w)) for w in word]

    return ' '.join(words).lstrip()

In [4]:
prep_pos(sample_kor , lang_ko)
prep_pos(sample_eng , lang_en)

[('영어', 'Noun'), ('문법', 'Noun'), ('은', 'Josa'), ('복잡하다', 'Adjective'), ('.', 'Punctuation')]


'영어 문법 복잡하다'

['english', 'grammer', 'complicated']


'english grammer complic'

In [5]:
# translate korean into english
import requests as req
import re
import json
from googletrans import Translator

import os, sys
import urllib.request
        
def translate(text, dest='en'):
    translator = Translator(service_urls=[
            'translate.google.com',
            'translate.google.co.kr',
        ])

    return translator.translate(text, dest).text

# print(translate(text='커피가 맛있어요'))    
print(translate(text='남자친구는 졸린가봐요. 자꾸 자네요.'))    

My boyfriend is sleepy. You keep going.


In [6]:
import gensim
from gensim import corpora

dictionary = gensim.corpora.Dictionary()
# print([dictionary.get(k) for k in dictionary.keys()])
    
def prep_input(text, lang):
    text = prep_pos(text, lang)
#     print(text)

    if lang == 'ko':
        text = translate(text)
#         print(text)
    dictionary.add_documents([text.split()])
    return dictionary.doc2idx(text.split())

prep_input(sample_kor, lang_ko)

[('영어', 'Noun'), ('문법', 'Noun'), ('은', 'Josa'), ('복잡하다', 'Adjective'), ('.', 'Punctuation')]
영어 문법 복잡하다
English grammar is complicated


[0, 2, 3, 1]

### Embedding

- in order to use CNN model, convert text words into 2d array with size of total dictionary size^2
- 결국 dictionary 사이즈의 one-hot encoding방식
- empty space with padding


In [ ]:
# def convert_shape(x):
#     size = math.ceil(math.sqrt(len(dictionary.keys())))
#     len_x = len(x)
#     x3d = []
#     for i in range(len_x):
#         row = x[i]
#         zero_arr = np.zeros(size * size)
#         zero_arr[:len(row)] += row
#         zero_arr = zero_arr.reshape([size, size, 1])
#     x3d.append(zero_arr)
    
#     return np.array(x3d)

In [ ]:
# # def predict(text, lang):
# X_input = prep_input(sample_kor, lang_ko)
# print(X_input)
# X_input = np.array(X_input)
# print(X_input)
# X_input = X_input.reshape(1, X_input.size)
# print(X_input)
# X_input = convert_shape(X_input)
# print(X_input)

### Load naver sentiment dataset

In [7]:
import pandas as pd

train = pd.read_csv('./dataset/ratings_train.txt', sep='\t')
train = train[['document', 'label']]
train.head()

document  label
0                                아 더빙.. 진짜 짜증나네요 목소리      0
1                  흠...포스터보고 초딩영화줄....오버연기조차 가볍지 않구나      1
2                                  너무재밓었다그래서보는것을추천한다      0
3                      교도소 이야기구먼 ..솔직히 재미는 없다..평점 조정      0
4  사이몬페그의 익살스런 연기가 돋보였던 영화!스파이더맨에서 늙어보이기만 했던 커스틴 ...      1

In [8]:
test = pd.read_csv('./dataset/ratings_test.txt', sep='\t')
test = train[['document', 'label']]
test.head()

document  label
0                                아 더빙.. 진짜 짜증나네요 목소리      0
1                  흠...포스터보고 초딩영화줄....오버연기조차 가볍지 않구나      1
2                                  너무재밓었다그래서보는것을추천한다      0
3                      교도소 이야기구먼 ..솔직히 재미는 없다..평점 조정      0
4  사이몬페그의 익살스런 연기가 돋보였던 영화!스파이더맨에서 늙어보이기만 했던 커스틴 ...      1

In [ ]:
train['english'] = train.document.map(lambda x: prep_input(x, lang_ko))
test['english'] = test.document.map(lambda x: prep_input(x, lang_ko))

[('아', 'Exclamation'), ('더빙', 'Noun'), ('..', 'Punctuation'), ('진짜', 'Noun'), ('짜증나네요', 'Adjective'), ('목소리', 'Noun')]
더빙 진짜 짜증나네요 목소리
Dubing is really annoying.
[('흠', 'Noun'), ('...', 'Punctuation'), ('포스터', 'Noun'), ('보고', 'Noun'), ('초딩', 'Noun'), ('영화', 'Noun'), ('줄', 'Noun'), ('....', 'Punctuation'), ('오버', 'Noun'), ('연기', 'Noun'), ('조차', 'Josa'), ('가볍지', 'Adjective'), ('않구나', 'Verb')]
포스터 보고 초딩 영화 오버 연기 가볍지 않구나
Posting reports Overdue movie overdubs Not light
[('너', 'Modifier'), ('무재', 'Noun'), ('밓었', 'Noun'), ('다그', 'Noun'), ('래서', 'Noun'), ('보는것을', 'Verb'), ('추천', 'Noun'), ('한', 'Josa'), ('다', 'Adverb')]
무재 밓었 다그 래서 보는것을 추천
I recommend you to look at it
[('교도소', 'Noun'), ('이야기', 'Noun'), ('구먼', 'Noun'), ('..', 'Punctuation'), ('솔직히', 'Adjective'), ('재미', 'Noun'), ('는', 'Josa'), ('없다', 'Adjective'), ('..', 'Punctuation'), ('평점', 'Noun'), ('조정', 'Noun')]
교도소 이야기 구먼 솔직히 재미 없다 평점 조정
The story of the prison
[('사이', 'Modifier'), ('몬페', 'Noun'), ('그', 'Determiner'), ('의', 'Noun'), ('익

Funny, boring, and the same food movie Barbette Supper Chai Nam Barbette dinner talk and funny food viewing, but this is not it.
[('절대', 'Noun'), ('평범한', 'Adjective'), ('영화', 'Noun'), ('가', 'Josa'), ('아닌', 'Adjective'), ('수작', 'Noun'), ('이라', 'Josa'), ('는걸', 'Noun'), ('말씀드립니다', 'Verb'), ('.', 'Punctuation')]
절대 평범한 영화 아닌 수작 는걸 말씀드립니다
I mean, it's not an ordinary movie.
[('주제', 'Noun'), ('는', 'Josa'), ('좋은데', 'Adjective'), ('중반', 'Noun'), ('부터', 'Josa'), ('지루하다', 'Adjective')]
주제 좋은데 중반 지루하다
It's a good subject.
[('다', 'Adverb'), ('짤랐을꺼', 'Noun'), ('야', 'Josa'), ('.', 'Punctuation'), ('그래서', 'Adverb'), ('납득', 'Noun'), ('할', 'Verb'), ('수', 'Noun'), ('없었던거야', 'Adjective'), ('..', 'Punctuation'), ('그럴꺼야', 'Adjective'), ('..', 'Punctuation'), ('꼭', 'Noun'), ('그랬던걸', 'Adjective'), ('꺼야', 'Verb'), ('..', 'Punctuation')]
짤랐을꺼 그래서 납득 없었던거야 그럴꺼야 그랬던걸 꺼야
I would have cut it out, so I did not get it.
[('kl', 'Alpha'), ('2', 'Number'), ('g', 'Alpha'), ('고추', 'Noun'), ('를', 'Josa'), ('털어', 'Verb'), 

Lisa Thargarn I want to be the master of the dragon, even though I might be incest, but it was the best Nice novel, the drama dragon is the coolest laugh Director Thor Dark World
[('영화', 'Noun'), ('가', 'Josa'), ('사람', 'Noun'), ('의', 'Josa'), ('영혼', 'Noun'), ('을', 'Josa'), ('어루만져', 'Verb'), ('줄', 'Noun'), ('수도', 'Noun'), ('있군요', 'Adjective'), ('거친', 'Verb'), ('세', 'Modifier'), ('상사', 'Noun'), ('를', 'Josa'), ('잠시', 'Noun'), ('잊고', 'Verb'), ('동화', 'Noun'), ('같은', 'Adjective'), ('영화', 'Noun'), ('에', 'Josa'), ('행복했네요', 'Adjective')]
영화 사람 영혼 어루만져 수도 있군요 거친 상사 잠시 잊고 동화 같은 영화 행복했네요
You might be able to touch the soul of a movie person.
[('야', 'Exclamation'), ('세르게이', 'Noun'), ('!', 'Punctuation'), ('작은', 'Adjective'), ('고추', 'Noun'), ('의', 'Josa'), ('매운', 'Adjective'), ('맛', 'Noun'), ('을', 'Josa'), ('보여주마', 'Verb'), ('!', 'Punctuation'), ('포퐁', 'Noun'), ('저그', 'Noun'), ('콩', 'Noun'), ('진호', 'Noun'), ('가', 'Josa'), ('간다', 'Noun')]
세르게이 작은 고추 매운 보여주마 포퐁 저그 진호 간다
Sergei Spicy Show of Little Pepp

I've seen it for two days, but it's funny, but if you try to put things in it, it's open, it's open wide and everyone is going in there or if you try to manipulate the text, it's going away.
[('졸작', 'Noun')]
졸작
Rubbish
[('재밋네', 'Noun'), ('요', 'Josa'), ('달팽이', 'Noun'), ('가', 'Josa'), ('빨', 'Noun'), ('라서', 'Josa'), ('더', 'Noun'), ('재밌었어요', 'Adjective')]
재밋네 달팽이 재밌었어요
Jasmine Your snail was fun.
[('어설픈', 'Adjective'), ('전개', 'Noun'), ('어이없는', 'Adjective'), ('결말', 'Noun')]
어설픈 전개 어이없는 결말
Bullish ending Endless ending
[('부패한', 'Adjective'), ('로마노프', 'Noun'), ('왕조', 'Noun'), ('를', 'Josa'), ('기리', 'Noun'), ('는', 'Josa'), ('뭣같', 'Noun'), ('은', 'Josa'), ('영화', 'Noun'), ('...', 'Punctuation'), ('온몸', 'Noun'), ('으로', 'Josa'), ('항거', 'Noun'), ('했던', 'Verb'), ('러시아', 'Noun'), ('민중', 'Noun'), ('들', 'Suffix'), ('이', 'Josa'), ('그저', 'Adverb'), ('폭도', 'Noun'), ('냐', 'Josa')]
부패한 로마노프 왕조 기리 뭣같 영화 온몸 항거 했던 러시아 민중 그저 폭도
The Romanov dictatorship, which was corrupt,
[('내용', 'Noun'), ('전개', 'Noun'), ('는', 'J

I was born and the first movie came out.
[('왕', 'Noun'), ('짜증', 'Noun'), ('.....', 'Punctuation'), ('아주', 'Noun'), ('전개', 'Noun'), ('를', 'Josa'), ('짬뽕', 'Noun'), ('으로', 'Josa'), ('믹스', 'Noun'), ('했구나', 'Verb'), ('...', 'Punctuation'), ('음향', 'Noun'), ('만', 'Josa'), ('무섭게', 'Adjective'), ('하네', 'Verb'), ('..', 'Punctuation'), ('하아', 'Exclamation')]
짜증 아주 전개 짬뽕 믹스 했구나 음향 무섭게 하네 하아
It was a very unpleasant chanpon mix.
[('솔직히', 'Adjective'), ('난', 'Noun'), ('별루더', 'Noun'), ('라', 'Josa'), ('시간', 'Noun'), ('낭비', 'Noun'), ('느낌', 'Noun')]
솔직히 별루더 시간 낭비 느낌
Frankly I feel like a waste of time
[('대박', 'Noun')]
대박
Jackpot
[('시청률', 'Noun'), ('기준', 'Noun'), ('이', 'Josa'), ('되는', 'Verb'), ('패널', 'Noun'), ('가구', 'Noun'), ('들', 'Suffix'), ('머', 'Noun'), ('하는거지', 'Verb'), ('명작', 'Noun'), ('드라마', 'Noun'), ('다', 'Adverb'), ('망치', 'Noun'), ('네', 'Josa'), ('ㅡㅡ', 'KoreanParticle'), ('내', 'Noun'), ('가', 'Josa'), ('다', 'Adverb'), ('서운하다', 'Adjective'), ('...', 'Punctuation')]
시청률 기준 되는 패널 가구 하는거지 명작 드라마 망치 ㅡㅡ

...

Wow, it's really not funny.
[('군대', 'Noun'), ('를', 'Josa'), ('갔다', 'Verb'), ('온', 'Noun'), ('것', 'Noun'), ('과', 'Josa'), ('그렇지', 'Adjective'), ('않은', 'Verb'), ('것', 'Noun'), ('과의', 'Josa'), ('차이점', 'Noun'), ('은', 'Josa'), ('말년', 'Noun'), ('병장', 'Noun'), ('과', 'Josa'), ('신참', 'Noun'), ('만큼이나', 'Josa'), ('차이', 'Noun'), ('가', 'Josa'), ('있다', 'Adjective'), ('.', 'Punctuation')]
군대 갔다 그렇지 않은 차이점 말년 병장 신참 차이 있다
The army went to the difference, not the last year,
[('타', 'Modifier'), ('마코', 'Noun'), ('마켓', 'Noun'), ('을', 'Josa'), ('끝', 'Noun'), ('까지', 'Josa'), ('보고나서', 'Verb'), ('남았던', 'Verb'), ('아쉬운', 'Adjective'), ('여운', 'Noun'), ('을', 'Josa'), ('이', 'Noun'), ('극장판', 'Noun'), ('이', 'Josa'), ('전부', 'Noun'), ('해결', 'Noun'), ('해줬다', 'Verb'), ('.', 'Punctuation'), ('보는', 'Verb'), ('내내', 'Noun'), ('가슴', 'Noun'), ('설렜고', 'Adjective'), ('캐릭터', 'Noun'), ('하나', 'Noun'), ('하나', 'Noun'), ('가', 'Josa'), ('정말', 'Noun'), ('다', 'Adverb'), ('귀여웠다', 'Adjective'), ('.', 'Punctuation')]
마코 마켓 보고나서 남았던 아쉬운 여운 극

Lee Sung-jae Park Hyun-jin I want to take a picture of the movie I do not think I would choose the actress first
[('둠스데이', 'Noun'), ('2014', 'Number'), ('와', 'Verb'), ('같은', 'Adjective'), ('급', 'Noun'), ('의', 'Josa'), ('영화', 'Noun'), ('.', 'Punctuation'), ('시간', 'Noun'), ('낭비', 'Noun'), ('마시오', 'Verb'), ('.', 'Punctuation')]
둠스데이 2014 같은 영화 시간 낭비 마시오
Do not waste movie time like Doomsday 2014
[('아', 'Exclamation'), ('오랜', 'Modifier'), ('만', 'Noun'), ('에', 'Josa'), ('제대로', 'Noun'), ('된', 'Verb'), ('영화', 'Noun'), ('한편', 'Noun'), ('잘', 'VerbPrefix'), ('봤네요', 'Verb'), ('이런게', 'Adjective'), ('영화', 'Noun'), ('지', 'Josa'), ('!', 'Punctuation'), ('유명배우', 'Noun'), ('나와서', 'Verb'), ('꽁', 'Adverb'), ('냥', 'Noun'), ('꽁', 'Adverb'), ('냥', 'Noun'), ('하', 'Suffix'), ('는', 'Josa'), ('시간', 'Noun'), ('낭비', 'Noun'), ('영화', 'Noun'), ('같은거', 'Adjective'), ('볼', 'Noun'), ('시간', 'Noun'), ('에', 'Josa'), ('이런거', 'Adjective'), ('한', 'Determiner'), ('편이', 'Noun'), ('나더', 'Verb'), ('봐야지', 'Verb'), ('!', 'Punctuat

Underground public telephone Called shivering shouting The film made a heartburn
[('우뢰', 'Noun'), ('메', 'Noun'), ('같은', 'Adjective'), ('CG', 'Alpha'), ('에', 'Josa'), ('연출', 'Noun'), ('도', 'Josa'), ('엉망', 'Noun'), ('이다', 'Josa'), ('...', 'Punctuation'), ('여기', 'Noun'), ('평점', 'Noun'), ('보고', 'Noun'), ('눈물난다는거', 'Verb'), ('알', 'Noun'), ('고', 'Josa'), ('봤는데', 'Verb'), ('나도', 'Verb'), ('울었다', 'Verb'), ('젠장', 'Noun'), (';;', 'Punctuation'), ('소취', 'Noun'), ('왜', 'Noun'), ('그랬어', 'Adjective'), ('ㅜㅜ', 'KoreanParticle'), ('나이', 'Noun'), ('가', 'Josa'), ('들어서', 'Verb'), ('눈물', 'Noun'), ('이', 'Josa'), ('많아진', 'Verb'), ('탓', 'Noun'), ('일까', 'Verb'), (';;', 'Punctuation'), ('ㅜㅜ', 'KoreanParticle')]
우뢰 같은 CG 연출 엉망 여기 평점 보고 눈물난다는거 봤는데 나도 울었다 젠장 소취 그랬어 ㅜㅜ 나이 들어서 눈물 많아진 일까 ㅜㅜ
Thunderstruck CG production mess I saw the rating here and I was tearing but I also cried Shit I did deodorant ㅜ ㅜ
[('제목', 'Noun'), ('만', 'Josa'), ('거창', 'Noun'), ('.', 'Punctuation'), ('비슷한시기에', 'Adjective'), ('제작', 'Noun'), ('된'

Charlotte gangster is pretty
[('진실', 'Noun'), ('은', 'Josa'), ('밝혀진다', 'Verb'), ('.', 'Punctuation')]
진실 밝혀진다
The truth is revealed.
[('시시하다', 'Adjective'), ('.', 'Punctuation'), ('강한', 'Adjective'), ('긴장감', 'Noun'), ('이', 'Josa'), ('없다', 'Adjective'), ('.', 'Punctuation')]
시시하다 강한 긴장감 없다
I do not have strong tension.
[('여자', 'Noun'), ('주인공', 'Noun'), ('이', 'Josa'), ('질질', 'Noun'), ('대', 'Suffix'), ('서', 'Josa'), ('이', 'Noun'), ('영화', 'Noun'), ('는', 'Josa'), ('1', 'Number'), ('점', 'Noun'), ('이다', 'Josa'), ('.', 'Punctuation'), ('너무', 'Adverb'), ('길고', 'Adjective'), ('지루하고', 'Adjective'), ('여자', 'Noun'), ('때매', 'Noun'), ('짜증난다', 'Adjective'), ('.', 'Punctuation')]
여자 주인공 질질 영화 너무 길고 지루하고 여자 때매 짜증난다
The main character of the woman The film is too long and tedious The woman is annoyed
[('역사', 'Noun'), ('도', 'Josa'), ('픽션', 'Noun'), ('도', 'Josa'), (',', 'Punctuation'), ('재미', 'Noun'), ('도', 'Josa'), ('의미', 'Noun'), ('도', 'Josa'), (',', 'Punctuation'), ('미스터리', 'Noun'), ('도', 'Josa'), ('드라마'

When you read top fantasy How wonderful story you read
[('매우', 'Noun'), ('재미있게', 'Adjective'), ('잘', 'Verb'), ('봤습니다', 'Verb')]
매우 재미있게 봤습니다
I've had a lot of fun.
[('그닥', 'Noun'), ('..', 'Punctuation'), ('이런', 'Adjective'), ('영화', 'Noun'), ('를', 'Josa'), ('왜', 'Noun'), ('만드는지', 'Verb'), ('...', 'Punctuation')]
그닥 이런 영화 만드는지
That's how I make a movie like this
[('시도', 'Noun'), ('만', 'Josa'), ('좋았다', 'Adjective'), ('..', 'Punctuation')]
시도 좋았다
It was good to try.
[('보수', 'Noun'), ('마초', 'Noun'), ('들', 'Suffix'), ('의', 'Josa'), ('겉멋', 'Noun'), ('쩌', 'Noun'), ('는', 'Josa'), ('비행', 'Noun'), ('질', 'Noun'), ('.', 'Punctuation')]
보수 마초 겉멋 비행
Conservative forage fly
[('한층', 'Noun'), ('더', 'Noun'), ('업그레이드', 'Noun'), ('된', 'Verb'), ('스케일', 'Noun'), (',', 'Punctuation'), ('여전한', 'Adjective'), ('뒤죽박죽', 'Noun'), ('유쾌한', 'Adjective'), ('대', 'Modifier'), ('소동', 'Noun'), ('!', 'Punctuation')]
한층 업그레이드 스케일 여전한 뒤죽박죽 유쾌한 소동
Upscale Upgrade Scale
[('역시', 'Noun'), ('...', 'Punctuation'), ('역시', 'Noun'), (

In [ ]:
train.head()

In [ ]:
max_words = len(dictionary.keys())
emotion_classes = ['positive', 'negative']
class_size = len(emotion_classes)

batch_size = 64
n_epoch = 10

In [ ]:
# train['cat_label'] = train.label.map(lambda x: [1, 0] if x==0 else [0, 1])
# train['y'] = 
train['test'] = np_utils.to_categorical(train.label, class_size)
# test['y'] = np_utils.to_categorical(test.label, class_size)

In [ ]:
from keras.datasets import imdb

In [ ]:
(X_tr, y_tr), (X_te, y_te) = imdb.load_data(num_words=5000)

In [ ]:
X_tr.shape

In [ ]:
X_tr[0]